***Model*** - 1

In [ ]:
# Step 1: Setup and Imports
!pip install xgboost pandas numpy scikit-learn

import os
import json
import pandas as pd
import numpy as np
from sklearn.metrics import accuracy_score
import xgboost as xgb
from google.colab import drive

drive.mount('/content/drive')
data_path = '/content/drive/My Drive/AI_Security_Project/EMBER2018'

# Step 2: Feature Extraction Function
def extract_features(sample):
    features = []
    features.extend(sample['histogram'])
    features.extend(sample['byteentropy'])
    features.append(sample['strings']['numstrings'])
    features.append(sample['strings']['avlength'])
    features.append(sample['strings']['printables'])
    features.append(sample['strings']['entropy'])
    features.append(sample['strings']['paths'])
    features.append(sample['strings']['urls'])
    features.append(sample['strings']['registry'])
    features.append(sample['strings']['MZ'])
    features.append(sample['general']['size'])
    features.append(sample['general']['vsize'])
    features.append(sample['general']['has_debug'])
    features.append(sample['general']['exports'])
    features.append(sample['general']['imports'])
    features.append(sample['general']['has_relocations'])
    features.append(sample['general']['has_resources'])
    features.append(sample['general']['has_signature'])
    features.append(sample['general']['has_tls'])
    features.append(sample['general']['symbols'])
    return features

# Step 3: Load Data Incrementally (Limit to 400,000 Samples)
def load_data(file_list, max_samples=400000):
    X, y = [], []
    total_samples = 0
    for file in file_list:
        file_path = os.path.join(data_path, file)
        print(f"Processing {file}...")
        with open(file_path, 'r') as f:
            for line in f:
                if total_samples >= max_samples:
                    break
                sample = json.loads(line.strip())
                if 'label' in sample and sample['label'] in [0, 1]:
                    X.append(extract_features(sample))
                    y.append(sample['label'])
                    total_samples += 1
        if total_samples >= max_samples:
            break
    return np.array(X), np.array(y)

train_files = [f'train_features_{i}.jsonl' for i in range(6)]
test_file = ['test_features.jsonl']

X_train, y_train = load_data(train_files, max_samples=400000)
X_test, y_test = load_data(test_file, max_samples=80000)  # 20% of train size

# Step 4: Train XGBoost Model
print("Training XGBoost model...")
xgb_model = xgb.XGBClassifier(
    objective='binary:logistic',
    n_estimators=100,
    max_depth=6,
    learning_rate=0.1,
    subsample=0.8,
    colsample_bytree=0.8,
    random_state=42,
    n_jobs=-1
)
xgb_model.fit(X_train, y_train)

# Step 5: Evaluate Model
y_pred = xgb_model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print(f"Model 1 Accuracy on Clean Test Data: {accuracy * 100:.2f}%")

# Step 6: Save Model and Datasets
xgb_model.save_model('/content/drive/My Drive/AI_Security_Project/xgb_model_1.json')
np.save('/content/drive/My Drive/AI_Security_Project/X_train_clean.npy', X_train)
np.save('/content/drive/My Drive/AI_Security_Project/y_train_clean.npy', y_train)
np.save('/content/drive/My Drive/AI_Security_Project/X_test.npy', X_test)
np.save('/content/drive/My Drive/AI_Security_Project/y_test.npy', y_test)
print("Model and datasets saved to Drive.")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Processing train_features_0.jsonl...
Processing train_features_1.jsonl...
Processing train_features_2.jsonl...
Processing train_features_3.jsonl...
Processing train_features_4.jsonl...
Processing test_features.jsonl...
Training XGBoost model...
Model 1 Accuracy on Clean Test Data: 88.70%
Model and datasets saved to Drive.


FGSM - Poisoning

In [ ]:
# Step 1: Setup and Imports
!pip install xgboost pandas numpy scikit-learn tensorflow==2.15.0

import numpy as np
from sklearn.metrics import accuracy_score
import xgboost as xgb
import tensorflow as tf
from tensorflow.keras import layers, models
from google.colab import drive

drive.mount('/content/drive')

# Step 2: Load Clean Data and Model 1
X_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/X_train_clean.npy')
y_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/y_train_clean.npy')
X_test = np.load('/content/drive/My Drive/AI_Security_Project/X_test.npy')
y_test = np.load('/content/drive/My Drive/AI_Security_Project/y_test.npy')
xgb_model = xgb.XGBClassifier()
xgb_model.load_model('/content/drive/My Drive/AI_Security_Project/xgb_model_1.json')

# Step 3: Surrogate Neural Network
def build_surrogate_model(input_dim):
    model = models.Sequential([
        layers.Input(shape=(input_dim,)),
        layers.Dense(256, activation='relu'),
        layers.Dense(128, activation='relu'),
        layers.Dense(64, activation='relu'),
        layers.Dense(1, activation='sigmoid')
    ])
    model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
    return model

X_train_normalized = (X_train_clean - X_train_clean.mean(axis=0)) / (X_train_clean.std(axis=0) + 1e-8)
surrogate_model = build_surrogate_model(X_train_normalized.shape[1])
surrogate_model.fit(X_train_normalized, y_train_clean, epochs=5, batch_size=32, verbose=1)

# Step 4: FGSM Attack
def fgsm_attack(X, y, model, epsilon=0.05):
    X_tensor = tf.convert_to_tensor(X, dtype=tf.float32)
    y_tensor = tf.convert_to_tensor(y, dtype=tf.float32)[:, tf.newaxis]
    with tf.GradientTape() as tape:
        tape.watch(X_tensor)
        predictions = model(X_tensor)
        loss = tf.keras.losses.binary_crossentropy(y_tensor, predictions)
    gradient = tape.gradient(loss, X_tensor)
    perturbation = epsilon * tf.sign(gradient)
    X_poisoned = X_tensor + perturbation
    return X_poisoned.numpy()

print("Generating FGSM poisoned data...")
X_train_fgsm = fgsm_attack(X_train_normalized, y_train_clean, surrogate_model, epsilon=0.05)

# Step 5: Retrain Model 1 and Evaluate
print("Retraining Model 1 on FGSM poisoned data...")
X_train_fgsm_denorm = X_train_fgsm * (X_train_clean.std(axis=0) + 1e-8) + X_train_clean.mean(axis=0)
xgb_model.fit(X_train_fgsm_denorm, y_train_clean)
y_pred = xgb_model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print(f"Accuracy on clean test data after FGSM poisoning: {accuracy * 100:.2f}%")

# Step 6: Save Poisoned Dataset
np.save('/content/drive/My Drive/AI_Security_Project/X_train_fgsm.npy', X_train_fgsm_denorm)
print("FGSM poisoned dataset saved to Drive.")

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 475.3/475.3 MB 2.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 41.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 37.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.6/294.6 kB 23.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.5/5.5 MB 60.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 442.0/442.0 kB 32.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.4/78.4 kB 7.3 MB/s eta 0:00:00
  Attempting uninstall: wrapt
    Found existing installation: wrapt 1.17.2
    Uninstalling wrapt-1.17.2:
      Successfully uninstalled wrapt-1.17.2
  Attempting uninstall: protobuf
    Found existing installation: protobuf 5.29.3
    Uninstalling protobuf-5.29.3:
      Successfully uninstalled protobuf-5.29.3
  Attempting uninstall: ml-dtypes
    Found existing installation: ml-dtypes 0.4.1
    Uninstalling ml-dtypes-0.4.1:
      Successfully

PGD - Poisoning

In [ ]:
# Step 1: Setup and Imports
!pip install xgboost pandas numpy scikit-learn tensorflow==2.15.0

import numpy as np
from sklearn.metrics import accuracy_score
import xgboost as xgb
import tensorflow as tf
from tensorflow.keras import layers, models
from google.colab import drive

drive.mount('/content/drive')

# Step 2: Load Clean Data and Model 1
X_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/X_train_clean.npy')
y_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/y_train_clean.npy')
X_test = np.load('/content/drive/My Drive/AI_Security_Project/X_test.npy')
y_test = np.load('/content/drive/My Drive/AI_Security_Project/y_test.npy')
xgb_model = xgb.XGBClassifier()
xgb_model.load_model('/content/drive/My Drive/AI_Security_Project/xgb_model_1.json')

# Step 3: Surrogate Neural Network
def build_surrogate_model(input_dim):
    model = models.Sequential([
        layers.Input(shape=(input_dim,)),
        layers.Dense(256, activation='relu'),
        layers.Dense(128, activation='relu'),
        layers.Dense(64, activation='relu'),
        layers.Dense(1, activation='sigmoid')
    ])
    model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
    return model

X_train_normalized = (X_train_clean - X_train_clean.mean(axis=0)) / (X_train_clean.std(axis=0) + 1e-8)
surrogate_model = build_surrogate_model(X_train_normalized.shape[1])
surrogate_model.fit(X_train_normalized, y_train_clean, epochs=5, batch_size=32, verbose=1)

# Step 4: PGD Attack with Batch Processing
def pgd_attack_batched(X, y, model, epsilon=0.1, alpha=0.03, num_iter=20, batch_size=50000):
    X_poisoned = X.copy()
    num_samples = X.shape[0]
    for start in range(0, num_samples, batch_size):
        end = min(start + batch_size, num_samples)
        X_batch = X[start:end]
        y_batch = y[start:end]

        X_tensor = tf.convert_to_tensor(X_batch, dtype=tf.float32)
        y_tensor = tf.convert_to_tensor(y_batch, dtype=tf.float32)[:, tf.newaxis]

        for _ in range(num_iter):
            with tf.GradientTape() as tape:
                tape.watch(X_tensor)
                predictions = model(X_tensor)
                loss = tf.keras.losses.binary_crossentropy(y_tensor, predictions)
            gradient = tape.gradient(loss, X_tensor)
            perturbation = alpha * tf.sign(gradient)
            X_tensor = X_tensor + perturbation
            X_tensor = tf.clip_by_value(X_tensor, X_batch - epsilon, X_batch + epsilon)

        X_poisoned[start:end] = X_tensor.numpy()
    return X_poisoned

print("Generating PGD poisoned data in batches...")
X_train_pgd = pgd_attack_batched(X_train_normalized, y_train_clean, surrogate_model, epsilon=0.1, alpha=0.03, num_iter=20, batch_size=50000)

# Step 5: Retrain Model 1 and Evaluate
print("Retraining Model 1 on PGD poisoned data...")
X_train_pgd_denorm = X_train_pgd * (X_train_clean.std(axis=0) + 1e-8) + X_train_clean.mean(axis=0)
xgb_model.fit(X_train_pgd_denorm, y_train_clean)
y_pred = xgb_model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print(f"Accuracy on clean test data after PGD poisoning: {accuracy * 100:.2f}%")

# Step 6: Save Poisoned Dataset
np.save('/content/drive/My Drive/AI_Security_Project/X_train_pgd.npy', X_train_pgd_denorm)
print("PGD poisoned dataset saved to Drive.")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Epoch 1/5
12500/12500 [==============================] - 36s 3ms/step - loss: 0.3391 - accuracy: 0.8504
Epoch 2/5
12500/12500 [==============================] - 36s 3ms/step - loss: 0.2743 - accuracy: 0.8804
Epoch 3/5
12500/12500 [==============================] - 33s 3ms/step - loss: 0.2479 - accuracy: 0.8938
Epoch 4/5
12500/12500 [==============================] - 33s 3ms/step - loss: 0.2316 - accuracy: 0.9018
Epoch 5/5
12500/12500 [==============================] - 33s 3ms/step - loss: 0.2188 - accuracy: 0.9075
Generating PGD poisoned data in batches...
Retraining Model 1 on PGD poisoned data...
Accuracy on clean test data after PGD poisoning: 57.22%
PGD poisoned dataset saved to Drive.


Backdoor

In [ ]:
# Step 1: Setup and Imports
!pip install xgboost pandas numpy scikit-learn

import numpy as np
from sklearn.metrics import accuracy_score
import xgboost as xgb
from google.colab import drive

drive.mount('/content/drive')

# Step 2: Load Clean Data and Model 1
X_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/X_train_clean.npy')
y_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/y_train_clean.npy')
X_test = np.load('/content/drive/My Drive/AI_Security_Project/X_test.npy')
y_test = np.load('/content/drive/My Drive/AI_Security_Project/y_test.npy')
xgb_model = xgb.XGBClassifier()
xgb_model.load_model('/content/drive/My Drive/AI_Security_Project/xgb_model_1.json')

# Step 3: Backdoor Attack
def backdoor_attack(X, y, poison_rate=0.2):
    X_poisoned = X.copy()
    y_poisoned = y.copy()
    num_poison = int(len(X) * poison_rate)
    indices = np.random.choice(np.where(y == 0)[0], num_poison, replace=False)
    X_poisoned[indices, 263] = 1000  # MZ trigger
    X_poisoned[indices, 256] = 5000  # numstrings trigger
    y_poisoned[indices] = 1
    return X_poisoned, y_poisoned

print("Generating backdoor poisoned data...")
X_train_backdoor, y_train_backdoor = backdoor_attack(X_train_clean, y_train_clean, poison_rate=0.2)

# Step 4: Retrain Model 1 and Evaluate
print("Retraining Model 1 on backdoor poisoned data...")
xgb_model.fit(X_train_backdoor, y_train_backdoor)
y_pred = xgb_model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print(f"Accuracy on clean test data after Backdoor poisoning: {accuracy * 100:.2f}%")

# Step 5: Save Poisoned Dataset
np.save('/content/drive/My Drive/AI_Security_Project/X_train_backdoor.npy', X_train_backdoor)
np.save('/content/drive/My Drive/AI_Security_Project/y_train_backdoor.npy', y_train_backdoor)
print("Backdoor poisoned dataset saved to Drive.")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Generating backdoor poisoned data...
Retraining Model 1 on backdoor poisoned data...
Accuracy on clean test data after Backdoor poisoning: 88.70%
Backdoor poisoned dataset saved to Drive.


Detector - 1

In [ ]:
# Step 1: Imports
!pip install scikit-learn numpy pandas
import numpy as np
from sklearn.ensemble import IsolationForest
from sklearn.metrics import roc_auc_score
from google.colab import drive
import pickle

drive.mount('/content/drive')

# Step 2: Load Saved Datasets
X_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/X_train_clean.npy')
X_train_fgsm = np.load('/content/drive/My Drive/AI_Security_Project/X_train_fgsm.npy')

# Step 3: Detector Function
def train_detector(X_clean, X_poisoned, attack_name):
    print(f"Training {attack_name} detector...")
    iso_forest = IsolationForest(contamination=0.1, random_state=42, n_estimators=100)
    iso_forest.fit(X_clean)

    clean_scores = iso_forest.decision_function(X_clean)
    clean_pred = iso_forest.predict(X_clean)
    poisoned_scores = iso_forest.decision_function(X_poisoned)
    poisoned_pred = iso_forest.predict(X_poisoned)

    clean_anomaly_rate = np.mean(clean_pred == -1) * 100
    poisoned_anomaly_rate = np.mean(poisoned_pred == -1) * 100

    print(f"{attack_name} Detector Results:")
    print(f"Clean data anomaly rate: {clean_anomaly_rate:.2f}%")
    print(f"Poisoned data anomaly rate: {poisoned_anomaly_rate:.2f}%")
    print(f"Detection: {'Poisoned' if poisoned_anomaly_rate > 5 else 'Clean'}")
    print(f"Estimated poisoning percentage: {poisoned_anomaly_rate:.2f}%")

    true_labels = np.concatenate([np.zeros(len(X_clean)), np.ones(len(X_poisoned))])
    scores = np.concatenate([clean_scores, poisoned_scores])
    auc = roc_auc_score(true_labels, -scores)
    print(f"AUC Score: {auc:.4f}")

    return iso_forest

# Step 4: Train and Test FGSM Detector
detector_fgsm = train_detector(X_train_clean, X_train_fgsm, "FGSM")

# Step 5: Save FGSM Detector
with open('/content/drive/My Drive/AI_Security_Project/detector_fgsm.pkl', 'wb') as f:
    pickle.dump(detector_fgsm, f)
print("FGSM detector saved to Drive.")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Training FGSM detector...
FGSM Detector Results:
Clean data anomaly rate: 10.00%
Poisoned data anomaly rate: 19.49%
Detection: Poisoned
Estimated poisoning percentage: 19.49%
AUC Score: 0.8296
FGSM detector saved to Drive.


Detector - 2

In [ ]:
# Step 1: Imports
!pip install scikit-learn numpy pandas
import numpy as np
from sklearn.ensemble import IsolationForest
from sklearn.metrics import roc_auc_score
from google.colab import drive
import pickle

drive.mount('/content/drive')

# Step 2: Load Saved Datasets
X_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/X_train_clean.npy')
X_train_pgd = np.load('/content/drive/My Drive/AI_Security_Project/X_train_pgd.npy')

# Step 3: Detector Function
def train_detector(X_clean, X_poisoned, attack_name):
    print(f"Training {attack_name} detector...")
    iso_forest = IsolationForest(contamination=0.1, random_state=42, n_estimators=100)
    iso_forest.fit(X_clean)

    clean_scores = iso_forest.decision_function(X_clean)
    clean_pred = iso_forest.predict(X_clean)
    poisoned_scores = iso_forest.decision_function(X_poisoned)
    poisoned_pred = iso_forest.predict(X_poisoned)

    clean_anomaly_rate = np.mean(clean_pred == -1) * 100
    poisoned_anomaly_rate = np.mean(poisoned_pred == -1) * 100

    print(f"{attack_name} Detector Results:")
    print(f"Clean data anomaly rate: {clean_anomaly_rate:.2f}%")
    print(f"Poisoned data anomaly rate: {poisoned_anomaly_rate:.2f}%")
    print(f"Detection: {'Poisoned' if poisoned_anomaly_rate > 5 else 'Clean'}")
    print(f"Estimated poisoning percentage: {poisoned_anomaly_rate:.2f}%")

    true_labels = np.concatenate([np.zeros(len(X_clean)), np.ones(len(X_poisoned))])
    scores = np.concatenate([clean_scores, poisoned_scores])
    auc = roc_auc_score(true_labels, -scores)
    print(f"AUC Score: {auc:.4f}")

    return iso_forest

# Step 4: Train and Test PGD Detector
detector_pgd = train_detector(X_train_clean, X_train_pgd, "PGD")

# Step 5: Save PGD Detector
with open('/content/drive/My Drive/AI_Security_Project/detector_pgd.pkl', 'wb') as f:
    pickle.dump(detector_pgd, f)
print("PGD detector saved to Drive.")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Training PGD detector...
PGD Detector Results:
Clean data anomaly rate: 10.00%
Poisoned data anomaly rate: 33.49%
Detection: Poisoned
Estimated poisoning percentage: 33.49%
AUC Score: 0.8945
PGD detector saved to Drive.


Detector - 3

In [ ]:
# Step 1: Imports
!pip install scikit-learn numpy pandas
import numpy as np
from sklearn.ensemble import IsolationForest
from sklearn.metrics import roc_auc_score
from google.colab import drive
import pickle

drive.mount('/content/drive')

# Step 2: Load Saved Datasets
X_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/X_train_clean.npy')
X_train_backdoor = np.load('/content/drive/My Drive/AI_Security_Project/X_train_backdoor.npy')

# Step 3: Detector Function
def train_detector(X_clean, X_poisoned, attack_name):
    print(f"Training {attack_name} detector...")
    iso_forest = IsolationForest(contamination=0.1, random_state=42, n_estimators=100)
    iso_forest.fit(X_clean)

    clean_scores = iso_forest.decision_function(X_clean)
    clean_pred = iso_forest.predict(X_clean)
    poisoned_scores = iso_forest.decision_function(X_poisoned)
    poisoned_pred = iso_forest.predict(X_poisoned)

    clean_anomaly_rate = np.mean(clean_pred == -1) * 100
    poisoned_anomaly_rate = np.mean(poisoned_pred == -1) * 100

    print(f"{attack_name} Detector Results:")
    print(f"Clean data anomaly rate: {clean_anomaly_rate:.2f}%")
    print(f"Poisoned data anomaly rate: {poisoned_anomaly_rate:.2f}%")
    print(f"Detection: {'Poisoned' if poisoned_anomaly_rate > 5 else 'Clean'}")
    print(f"Estimated poisoning percentage: {poisoned_anomaly_rate:.2f}%")

    true_labels = np.concatenate([np.zeros(len(X_clean)), np.ones(len(X_poisoned))])
    scores = np.concatenate([clean_scores, poisoned_scores])
    auc = roc_auc_score(true_labels, -scores)
    print(f"AUC Score: {auc:.4f}")

    return iso_forest

# Step 4: Train and Test Backdoor Detector
detector_backdoor = train_detector(X_train_clean, X_train_backdoor, "Backdoor")

# Step 5: Save Backdoor Detector
with open('/content/drive/My Drive/AI_Security_Project/detector_backdoor.pkl', 'wb') as f:
    pickle.dump(detector_backdoor, f)
print("Backdoor detector saved to Drive.")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Training Backdoor detector...
Backdoor Detector Results:
Clean data anomaly rate: 10.00%
Poisoned data anomaly rate: 10.02%
Detection: Poisoned
Estimated poisoning percentage: 10.02%
AUC Score: 0.5162
Backdoor detector saved to Drive.


BEAST - FGSM - DETECTOR

In [ ]:
# Step 1: Install Libraries
!pip install scikit-learn numpy pandas tensorflow==2.15.0 adversarial-robustness-toolbox lightgbm
!pip install torch==2.5.1+cu124 -f https://download.pytorch.org/whl/torch_stable.html
!pip install torch-geometric -f https://pytorch-geometric.com/whl/torch-2.5.1+cu124.html

import numpy as np
import tensorflow as tf
from tensorflow.keras import layers, Model
from sklearn.ensemble import IsolationForest
from sklearn.metrics import roc_auc_score
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from art.attacks.evasion import FastGradientMethod
from art.estimators.classification import SklearnClassifier
import torch
from torch_geometric.nn import GCNConv
from torch_geometric.data import Data
from scipy.sparse import csr_matrix
import lightgbm as lgb
from google.colab import drive
import pickle
import os

drive.mount('/content/drive')

# Step 2: Load Data (FGSM Only)
X_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/X_train_clean.npy')
X_train_fgsm = np.load('/content/drive/My Drive/AI_Security_Project/X_train_fgsm.npy')
y_full = np.load('/content/drive/My Drive/AI_Security_Project/y_train_clean.npy')

# Step 3: Deep Denoising Autoencoder (DDAE) with Data Pipeline
def build_ddae(input_dim):
    inputs = layers.Input(shape=(input_dim,))
    enc = layers.Dense(128, activation='relu')(inputs)
    enc = layers.Dense(64, activation='relu')(enc)
    latent = layers.Dense(32, activation='relu')(enc)
    dec = layers.Dense(64, activation='relu')(latent)
    dec = layers.Dense(128, activation='relu')(dec)
    outputs = layers.Dense(input_dim, activation='linear')(dec)
    model = Model(inputs, outputs)
    model.compile(optimizer='adam', loss='mse')
    return model

ddae = build_ddae(X_train_clean.shape[1])
dataset = tf.data.Dataset.from_tensor_slices((X_train_clean, X_train_clean)).batch(40000).prefetch(tf.data.AUTOTUNE)
ddae.fit(dataset, epochs=5, verbose=1)

def get_ddae_scores(X, model, batch_size=40000, output_file='ddae_scores.npy'):
    scores = []
    dataset = tf.data.Dataset.from_tensor_slices(X).batch(batch_size).prefetch(tf.data.AUTOTUNE)
    for batch in dataset:
        recon = model.predict(batch, verbose=0)
        batch_scores = np.mean((batch.numpy() - recon) ** 2, axis=1)
        scores.append(batch_scores)
    scores = np.concatenate(scores)
    np.save(output_file, scores)
    return scores

# Step 4: Batch-Specific GNN
class GNN(torch.nn.Module):
    def __init__(self, in_channels):
        super(GNN, self).__init__()
        self.conv1 = GCNConv(in_channels, 64)
        self.conv2 = GCNConv(64, 32)
        self.out = torch.nn.Linear(32, 1)

    def forward(self, x, edge_index):
        x = self.conv1(x, edge_index).relu()
        x = self.conv2(x, edge_index).relu()
        return self.out(x)

gnn = GNN(X_train_clean.shape[1])
optimizer = torch.optim.Adam(gnn.parameters(), lr=0.01)
criterion = torch.nn.MSELoss()

def build_gnn_data_batch(X_batch):
    from sklearn.neighbors import kneighbors_graph
    adj = kneighbors_graph(X_batch, n_neighbors=3, mode='connectivity', include_self=False)
    edge_index = torch.tensor(np.array(csr_matrix(adj).nonzero()), dtype=torch.long)
    return Data(x=torch.tensor(X_batch, dtype=torch.float), edge_index=edge_index)

for epoch in range(5):
    gnn.train()
    batch_size = 40000
    total_loss = 0
    for i in range(0, len(X_train_clean), batch_size):
        X_batch = X_train_clean[i:i+batch_size]
        gnn_data_batch = build_gnn_data_batch(X_batch)
        optimizer.zero_grad()
        out = gnn(gnn_data_batch.x, gnn_data_batch.edge_index)
        loss = criterion(out, gnn_data_batch.x[:, :1])
        loss.backward()
        optimizer.step()
        total_loss += loss.item()
    print(f"Epoch {epoch+1}, Avg Batch Loss: {total_loss / (len(X_train_clean) // batch_size):.4f}")

def get_gnn_scores(X, gnn, batch_size=40000, output_file='gnn_scores.npy'):
    gnn.eval()
    scores = []
    for i in range(0, len(X), batch_size):
        X_batch = X[i:i+batch_size]
        gnn_data_batch = build_gnn_data_batch(X_batch)
        with torch.no_grad():
            batch_scores = gnn(gnn_data_batch.x, gnn_data_batch.edge_index).numpy().flatten()
        scores.append(batch_scores)
    scores = np.concatenate(scores)
    np.save(output_file, scores)
    return scores

# Step 5: Adversarial Feature Augmentation (AFA) with ART
X_subset, _, y_subset, _ = train_test_split(X_train_clean, y_full, train_size=10000, stratify=y_full, random_state=42)
scaler = StandardScaler()
X_subset_scaled = scaler.fit_transform(X_subset)

surrogate_model = LogisticRegression(max_iter=1000, solver='lbfgs')
surrogate_model.fit(X_subset_scaled, y_subset)

art_classifier = SklearnClassifier(model=surrogate_model)
fgsm_aug = FastGradientMethod(estimator=art_classifier, eps=0.1)
X_train_clean_scaled = scaler.transform(X_train_clean[:10000])
X_aug_fgsm = fgsm_aug.generate(X_train_clean_scaled)
X_augmented = np.vstack([X_train_clean[:10000], scaler.inverse_transform(X_aug_fgsm)])

# Step 6: FGSM Beast Detector with Fixed Ensemble Logic
def fgsm_beast_detector(X_clean, X_poisoned):
    print("Training FGSM Beast Detector...")

    # DDAE Scores
    ddae_clean_scores = get_ddae_scores(X_clean, ddae, output_file='/content/ddae_clean_fgsm.npy')
    ddae_poisoned_scores = get_ddae_scores(X_poisoned, ddae, output_file='/content/ddae_poisoned_fgsm.npy')

    # GNN Scores
    gnn_clean_scores = get_gnn_scores(X_clean, gnn, output_file='/content/gnn_clean_fgsm.npy')
    gnn_poisoned_scores = get_gnn_scores(X_poisoned, gnn, output_file='/content/gnn_poisoned_fgsm.npy')

    # Isolation Forest
    iso_forest = IsolationForest(contamination=0.5, random_state=42, n_estimators=100)
    iso_forest.fit(np.vstack([X_clean[:50000], X_augmented]))
    iso_clean_scores = -iso_forest.decision_function(X_clean)
    iso_poisoned_scores = -iso_forest.decision_function(X_poisoned)
    np.save('/content/iso_clean_fgsm.npy', iso_clean_scores)
    np.save('/content/iso_poisoned_fgsm.npy', iso_poisoned_scores)

    # Ensemble with LightGBM - Balanced Chunked Training
    batch_size = 100000  # 50,000 clean + 50,000 poisoned per chunk
    n_chunks = len(X_clean) // (batch_size // 2)  # Number of full chunks
    y_ensemble = np.concatenate([np.zeros(len(X_clean)), np.ones(len(X_poisoned))])
    lgb_model = lgb.LGBMClassifier(n_estimators=50, learning_rate=0.05)

    for i in range(n_chunks):
        clean_start = i * (batch_size // 2)
        clean_end = (i + 1) * (batch_size // 2)
        poisoned_start = i * (batch_size // 2)
        poisoned_end = (i + 1) * (batch_size // 2)

        clean_chunk = np.vstack([np.load('/content/ddae_clean_fgsm.npy')[clean_start:clean_end],
                                 np.load('/content/gnn_clean_fgsm.npy')[clean_start:clean_end],
                                 np.load('/content/iso_clean_fgsm.npy')[clean_start:clean_end]]).T
        poisoned_chunk = np.vstack([np.load('/content/ddae_poisoned_fgsm.npy')[poisoned_start:poisoned_end],
                                    np.load('/content/gnn_poisoned_fgsm.npy')[poisoned_start:poisoned_end],
                                    np.load('/content/iso_poisoned_fgsm.npy')[poisoned_start:poisoned_end]]).T

        X_chunk = np.vstack([clean_chunk, poisoned_chunk])
        y_chunk = np.concatenate([np.zeros(len(clean_chunk)), np.ones(len(poisoned_chunk))])

        if i == 0:
            lgb_model.fit(X_chunk, y_chunk)
        else:
            lgb_model.fit(X_chunk, y_chunk, init_model=lgb_model)

    # Final Predictions in Chunks
    clean_pred = []
    poisoned_pred = []
    for i in range(0, len(X_clean), batch_size):
        chunk = np.vstack([np.load('/content/ddae_clean_fgsm.npy')[i:i+batch_size],
                           np.load('/content/gnn_clean_fgsm.npy')[i:i+batch_size],
                           np.load('/content/iso_clean_fgsm.npy')[i:i+batch_size]]).T
        clean_pred.append(lgb_model.predict_proba(chunk)[:, 1])
    for i in range(0, len(X_poisoned), batch_size):
        chunk = np.vstack([np.load('/content/ddae_poisoned_fgsm.npy')[i:i+batch_size],
                           np.load('/content/gnn_poisoned_fgsm.npy')[i:i+batch_size],
                           np.load('/content/iso_poisoned_fgsm.npy')[i:i+batch_size]]).T
        poisoned_pred.append(lgb_model.predict_proba(chunk)[:, 1])

    clean_pred = np.concatenate(clean_pred)
    poisoned_pred = np.concatenate(poisoned_pred)

    clean_anomaly_rate = np.mean(clean_pred > 0.5) * 100
    poisoned_anomaly_rate = np.mean(poisoned_pred > 0.5) * 100

    print("FGSM Beast Detector Results:")
    print(f"Clean data anomaly rate: {clean_anomaly_rate:.2f}%")
    print(f"Poisoned data anomaly rate: {poisoned_anomaly_rate:.2f}%")
    print(f"Detection: {'Poisoned' if poisoned_anomaly_rate > 5 else 'Clean'}")
    print(f"Estimated poisoning percentage: {poisoned_anomaly_rate:.2f}%")

    auc = roc_auc_score(y_ensemble, np.concatenate([clean_pred, poisoned_pred]))
    print(f"AUC Score: {auc:.4f}")

    # Clean up
    for f in ['ddae_clean_fgsm.npy', 'ddae_poisoned_fgsm.npy', 'gnn_clean_fgsm.npy', 'gnn_poisoned_fgsm.npy', 'iso_clean_fgsm.npy', 'iso_poisoned_fgsm.npy']:
        os.remove(f'/content/{f}')

    return lgb_model, iso_forest, ddae, gnn

# Step 7: Train and Save FGSM Detector
detector_fgsm, iso_fgsm, ddae_fgsm, gnn_fgsm = fgsm_beast_detector(X_train_clean, X_train_fgsm)
with open('/content/drive/My Drive/AI_Security_Project/beast_detector_fgsm.pkl', 'wb') as f:
    pickle.dump(detector_fgsm, f)
print("FGSM Beast Detector saved to Drive.")

Looking in links: https://download.pytorch.org/whl/torch_stable.html
ERROR: Could not find a version that satisfies the requirement torch==2.5.1+cu124 (from versions: 1.13.0, 1.13.0+cpu, 1.13.0+cu116, 1.13.0+cu117, 1.13.0+cu117.with.pypi.cudnn, 1.13.1, 1.13.1+cpu, 1.13.1+cu116, 1.13.1+cu117, 1.13.1+cu117.with.pypi.cudnn, 2.0.0, 2.0.0+cpu, 2.0.0+cpu.cxx11.abi, 2.0.0+cu117, 2.0.0+cu117.with.pypi.cudnn, 2.0.0+cu118, 2.0.1, 2.0.1+cpu, 2.0.1+cpu.cxx11.abi, 2.0.1+cu117, 2.0.1+cu117.with.pypi.cudnn, 2.0.1+cu118, 2.0.1+rocm5.3, 2.0.1+rocm5.4.2, 2.1.0, 2.1.0+cpu, 2.1.0+cpu.cxx11.abi, 2.1.0+cu118, 2.1.0+cu121, 2.1.0+cu121.with.pypi.cudnn, 2.1.0+rocm5.5, 2.1.0+rocm5.6, 2.1.1, 2.1.1+cpu, 2.1.1+cpu.cxx11.abi, 2.1.1+cu118, 2.1.1+cu121, 2.1.1+cu121.with.pypi.cudnn, 2.1.1+rocm5.5, 2.1.1+rocm5.6, 2.1.2, 2.1.2+cpu, 2.1.2+cpu.cxx11.abi, 2.1.2+cu118, 2.1.2+cu121, 2.1.2+cu121.with.pypi.cudnn, 2.1.2+rocm5.5, 2.1.2+rocm5.6, 2.2.0, 2.2.0+cpu, 2.2.0+cpu.cxx11.abi, 2.2.0+cu118, 2.2.0+cu121, 2.2.0+rocm5.6, 2.2.0

/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/sklearn/ut

FGSM Beast Detector Results:
Clean data anomaly rate: 6.59%
Poisoned data anomaly rate: 96.22%
Detection: Poisoned
Estimated poisoning percentage: 96.22%
AUC Score: 0.9904
FGSM Beast Detector saved to Drive.


BEASTEST - FGSM - DETECTOR

In [ ]:
# Step 1: Install Libraries
!pip install scikit-learn numpy pandas tensorflow==2.15.0 adversarial-robustness-toolbox lightgbm
!pip install torch==2.5.1 -f https://download.pytorch.org/whl/torch_stable.html  # Adjusted to available version
!pip install torch-geometric

import numpy as np
import tensorflow as tf
from tensorflow.keras import layers, Model
from sklearn.ensemble import IsolationForest
from sklearn.metrics import roc_auc_score
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from art.attacks.evasion import FastGradientMethod
from art.estimators.classification import SklearnClassifier
import torch
from torch_geometric.nn import GCNConv
from torch_geometric.data import Data
from scipy.sparse import csr_matrix
import lightgbm as lgb
from google.colab import drive
import pickle
import os

drive.mount('/content/drive')

# Step 2: Load Data (FGSM Only)
X_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/X_train_clean.npy')
X_train_fgsm = np.load('/content/drive/My Drive/AI_Security_Project/X_train_fgsm.npy')
y_full = np.load('/content/drive/My Drive/AI_Security_Project/y_train_clean.npy')

# Step 3: Deep Denoising Autoencoder (DDAE) with Data Pipeline
def build_ddae(input_dim):
    inputs = layers.Input(shape=(input_dim,))
    enc = layers.Dense(128, activation='relu')(inputs)
    enc = layers.Dense(64, activation='relu')(enc)
    latent = layers.Dense(32, activation='relu')(enc)
    dec = layers.Dense(64, activation='relu')(latent)
    dec = layers.Dense(128, activation='relu')(dec)
    outputs = layers.Dense(input_dim, activation='linear')(dec)
    model = Model(inputs, outputs)
    model.compile(optimizer='adam', loss='mse')
    return model

ddae = build_ddae(X_train_clean.shape[1])
dataset = tf.data.Dataset.from_tensor_slices((X_train_clean, X_train_clean)).batch(40000).prefetch(tf.data.AUTOTUNE)
ddae.fit(dataset, epochs=5, verbose=1)
with open('/content/drive/My Drive/AI_Security_Project/ddae_fgsm.pkl', 'wb') as f:
    pickle.dump(ddae, f)

def get_ddae_scores(X, model, batch_size=40000, output_file='ddae_scores.npy'):
    scores = []
    dataset = tf.data.Dataset.from_tensor_slices(X).batch(batch_size).prefetch(tf.data.AUTOTUNE)
    for batch in dataset:
        recon = model.predict(batch, verbose=0)
        batch_scores = np.mean((batch.numpy() - recon) ** 2, axis=1)
        scores.append(batch_scores)
    scores = np.concatenate(scores)
    np.save(output_file, scores)
    return scores

# Step 4: Batch-Specific GNN
class GNN(torch.nn.Module):
    def __init__(self, in_channels):
        super(GNN, self).__init__()
        self.conv1 = GCNConv(in_channels, 64)
        self.conv2 = GCNConv(64, 32)
        self.out = torch.nn.Linear(32, 1)

    def forward(self, x, edge_index):
        x = self.conv1(x, edge_index).relu()
        x = self.conv2(x, edge_index).relu()
        return self.out(x)

gnn = GNN(X_train_clean.shape[1])
optimizer = torch.optim.Adam(gnn.parameters(), lr=0.01)
criterion = torch.nn.MSELoss()
for epoch in range(5):
    gnn.train()
    batch_size = 40000
    total_loss = 0
    for i in range(0, len(X_train_clean), batch_size):
        X_batch = X_train_clean[i:i+batch_size]
        gnn_data_batch = build_gnn_data_batch(X_batch)
        optimizer.zero_grad()
        out = gnn(gnn_data_batch.x, gnn_data_batch.edge_index)
        loss = criterion(out, gnn_data_batch.x[:, :1])
        loss.backward()
        optimizer.step()
        total_loss += loss.item()
    print(f"Epoch {epoch+1}, Avg Batch Loss: {total_loss / (len(X_train_clean) // batch_size):.4f}")
torch.save(gnn.state_dict(), '/content/drive/My Drive/AI_Security_Project/gnn_fgsm.pth')

def build_gnn_data_batch(X_batch):
    from sklearn.neighbors import kneighbors_graph
    adj = kneighbors_graph(X_batch, n_neighbors=3, mode='connectivity', include_self=False)
    edge_index = torch.tensor(np.array(csr_matrix(adj).nonzero()), dtype=torch.long)
    return Data(x=torch.tensor(X_batch, dtype=torch.float), edge_index=edge_index)

def get_gnn_scores(X, gnn, batch_size=40000, output_file='gnn_scores.npy'):
    gnn.eval()
    scores = []
    for i in range(0, len(X), batch_size):
        X_batch = X[i:i+batch_size]
        gnn_data_batch = build_gnn_data_batch(X_batch)
        with torch.no_grad():
            batch_scores = gnn(gnn_data_batch.x, gnn_data_batch.edge_index).numpy().flatten()
        scores.append(batch_scores)
    scores = np.concatenate(scores)
    np.save(output_file, scores)
    return scores

# Step 5: Adversarial Feature Augmentation (AFA) with ART
X_subset, _, y_subset, _ = train_test_split(X_train_clean, y_full, train_size=10000, stratify=y_full, random_state=42)
scaler = StandardScaler()
X_subset_scaled = scaler.fit_transform(X_subset)

surrogate_model = LogisticRegression(max_iter=1000, solver='lbfgs')
surrogate_model.fit(X_subset_scaled, y_subset)

art_classifier = SklearnClassifier(model=surrogate_model)
fgsm_aug = FastGradientMethod(estimator=art_classifier, eps=0.1)
X_train_clean_scaled = scaler.transform(X_train_clean[:10000])
X_aug_fgsm = fgsm_aug.generate(X_train_clean_scaled)
X_augmented = np.vstack([X_train_clean[:10000], scaler.inverse_transform(X_aug_fgsm)])

# Step 6: FGSM Beast Detector with Incremental Learning
class AdaptiveWeightLearner(tf.keras.Model):
    def __init__(self):
        super(AdaptiveWeightLearner, self).__init__()
        self.dense1 = layers.Dense(16, activation='relu')
        self.dense2 = layers.Dense(3, activation='softmax')  # Weights for DDAE, GNN, Iso

    def call(self, inputs):
        x = self.dense1(inputs)
        return self.dense2(x)

adaptive_learner = AdaptiveWeightLearner()
adaptive_learner.build(input_shape=(None, 3))  # Initialize variables
weight_file = '/content/drive/My Drive/AI_Security_Project/adaptive_weights_fgsm.h5'

def fgsm_beast_detector(X_clean, X_poisoned, incremental=True):
    print("Training FGSM Beast Detector...")

    # DDAE Scores
    ddae_clean_scores = get_ddae_scores(X_clean, ddae, output_file='/content/ddae_clean_fgsm.npy')
    ddae_poisoned_scores = get_ddae_scores(X_poisoned, ddae, output_file='/content/ddae_poisoned_fgsm.npy')

    # GNN Scores
    gnn_clean_scores = get_gnn_scores(X_clean, gnn, output_file='/content/gnn_clean_fgsm.npy')
    gnn_poisoned_scores = get_gnn_scores(X_poisoned, gnn, output_file='/content/gnn_poisoned_fgsm.npy')

    # Isolation Forest
    iso_forest = IsolationForest(contamination=0.5, random_state=42, n_estimators=100)
    iso_forest.fit(np.vstack([X_clean[:50000], X_augmented]))
    iso_clean_scores = -iso_forest.decision_function(X_clean)
    iso_poisoned_scores = -iso_forest.decision_function(X_poisoned)
    np.save('/content/iso_clean_fgsm.npy', iso_clean_scores)
    np.save('/content/iso_poisoned_fgsm.npy', iso_poisoned_scores)

    # Ensemble with LightGBM - Incremental Training
    batch_size = 100000
    X_ensemble_clean = np.vstack([ddae_clean_scores, gnn_clean_scores, iso_clean_scores]).T
    X_ensemble_poisoned = np.vstack([ddae_poisoned_scores, gnn_poisoned_scores, iso_poisoned_scores]).T
    X_ensemble = np.vstack([X_ensemble_clean, X_ensemble_poisoned])
    y_ensemble = np.concatenate([np.zeros(len(X_clean)), np.ones(len(X_poisoned))])

    # Shuffle for balanced chunks
    indices = np.random.permutation(len(X_ensemble))
    X_ensemble = X_ensemble[indices]
    y_ensemble = y_ensemble[indices]

    # Load or initialize LightGBM
    lgb_file = '/content/drive/My Drive/AI_Security_Project/beast_detector_fgsm.pkl'
    if os.path.exists(lgb_file) and incremental:
        with open(lgb_file, 'rb') as f:
            lgb_model = pickle.load(f)
    else:
        lgb_model = lgb.LGBMClassifier(n_estimators=50, learning_rate=0.05)

    # Adaptive weighting
    if not os.path.exists(weight_file):
        adaptive_learner.compile(optimizer='adam', loss='categorical_crossentropy')
        weights = np.ones((len(X_ensemble), 3)) / 3  # Initial equal weights
        adaptive_learner.fit(X_ensemble, weights, epochs=5, batch_size=10000, verbose=1)
    weights = adaptive_learner.predict(X_ensemble, batch_size=10000)
    adaptive_learner.save_weights(weight_file)

    # Weighted scores
    X_ensemble_weighted = np.sum(X_ensemble * weights, axis=1)

    # Incremental Training
    for i in range(0, len(X_ensemble), batch_size):
        X_chunk = X_ensemble[i:i+batch_size]
        y_chunk = y_ensemble[i:i+batch_size]
        if i == 0 or not incremental or not os.path.exists(lgb_file):
            lgb_model.fit(X_chunk, y_chunk)
        else:
            lgb_model.fit(X_chunk, y_chunk, init_model=lgb_model)

    # Final Predictions
    clean_pred = lgb_model.predict_proba(X_ensemble_clean)[:, 1]
    poisoned_pred = lgb_model.predict_proba(X_ensemble_poisoned)[:, 1]

    clean_anomaly_rate = np.mean(clean_pred > 0.5) * 100
    poisoned_anomaly_rate = np.mean(poisoned_pred > 0.5) * 100

    print("FGSM Beast Detector Results:")
    print(f"Clean data anomaly rate: {clean_anomaly_rate:.2f}%")
    print(f"Poisoned data anomaly rate: {poisoned_anomaly_rate:.2f}%")
    print(f"Detection: {'Poisoned' if poisoned_anomaly_rate > 5 else 'Clean'}")
    print(f"Estimated poisoning percentage: {poisoned_anomaly_rate:.2f}%")

    auc = roc_auc_score(y_ensemble, np.concatenate([clean_pred, poisoned_pred]))
    print(f"AUC Score: {auc:.4f}")

    # Clean up
    for f in ['ddae_clean_fgsm.npy', 'ddae_poisoned_fgsm.npy', 'gnn_clean_fgsm.npy', 'gnn_poisoned_fgsm.npy', 'iso_clean_fgsm.npy', 'iso_poisoned_fgsm.npy']:
        os.remove(f'/content/{f}')

    return lgb_model, iso_forest, ddae, gnn

# Step 7: Train and Save FGSM Detector
detector_fgsm, iso_fgsm, ddae_fgsm, gnn_fgsm = fgsm_beast_detector(X_train_clean, X_train_fgsm)
with open('/content/drive/My Drive/AI_Security_Project/beast_detector_fgsm.pkl', 'wb') as f:
    pickle.dump(detector_fgsm, f)
print("FGSM Beast Detector saved to Drive.")

Looking in links: https://download.pytorch.org/whl/torch_stable.html
Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Epoch 1/5
10/10 [==============================] - 16s 1s/step - loss: 316723200000.0000
Epoch 2/5
10/10 [==============================] - 15s 1s/step - loss: 271626960896.0000
Epoch 3/5
10/10 [==============================] - 15s 1s/step - loss: 161772355584.0000
Epoch 4/5
10/10 [==============================] - 15s 1s/step - loss: 91387469824.0000
Epoch 5/5
10/10 [==============================] - 14s 1s/step - loss: 50886733824.0000
Epoch 1, Avg Batch Loss: 428741161779.2000
Epoch 2, Avg Batch Loss: 376092722790.4000
Epoch 3, Avg Batch Loss: 264095469568.0000
Epoch 4, Avg Batch Loss: 238966815948.8000
Epoch 5, Avg Batch Loss: 239758596505.6000
Training FGSM Beast Detector...
80/80 [==============================] - 0s 2ms/step
[LightGBM] [Info] Number of positive: 50184, number of nega

/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(


FGSM Beast Detector Results:
Clean data anomaly rate: 5.21%
Poisoned data anomaly rate: 95.88%
Detection: Poisoned
Estimated poisoning percentage: 95.88%
AUC Score: 0.4988
FGSM Beast Detector saved to Drive.


BEASTEST - FSGM - Has to be executed

In [ ]:
# Step 1: Install Libraries
!pip install scikit-learn numpy pandas tensorflow==2.15.0 adversarial-robustness-toolbox lightgbm
!pip install torch==2.5.1 -f https://download.pytorch.org/whl/torch_stable.html
!pip install torch-geometric

import numpy as np
import tensorflow as tf
from tensorflow.keras import layers, Model
from sklearn.ensemble import IsolationForest
from sklearn.metrics import roc_auc_score
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from art.attacks.evasion import FastGradientMethod
from art.estimators.classification import SklearnClassifier
import torch
from torch_geometric.nn import GCNConv
from torch_geometric.data import Data
from scipy.sparse import csr_matrix
import lightgbm as lgb
from google.colab import drive
import pickle
import os

drive.mount('/content/drive')

# Step 2: Load Data (FGSM Only)
X_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/X_train_clean.npy')
X_train_fgsm = np.load('/content/drive/My Drive/AI_Security_Project/X_train_fgsm.npy')
y_full = np.load('/content/drive/My Drive/AI_Security_Project/y_train_clean.npy')

# Step 3: Deep Denoising Autoencoder (DDAE)
def build_ddae(input_dim):
    inputs = layers.Input(shape=(input_dim,))
    enc = layers.Dense(128, activation='relu')(inputs)
    enc = layers.Dense(64, activation='relu')(enc)
    latent = layers.Dense(32, activation='relu')(enc)
    dec = layers.Dense(64, activation='relu')(latent)
    dec = layers.Dense(128, activation='relu')(dec)
    outputs = layers.Dense(input_dim, activation='linear')(dec)
    model = Model(inputs, outputs)
    model.compile(optimizer='adam', loss='mse')
    return model

ddae = build_ddae(X_train_clean.shape[1])
dataset = tf.data.Dataset.from_tensor_slices((X_train_clean, X_train_clean)).batch(40000).prefetch(tf.data.AUTOTUNE)
ddae.fit(dataset, epochs=5, verbose=1)
with open('/content/drive/My Drive/AI_Security_Project/ddae_fgsm.pkl', 'wb') as f:
    pickle.dump(ddae, f)

def get_ddae_scores(X, model, batch_size=40000, output_file='ddae_scores.npy'):
    scores = []
    dataset = tf.data.Dataset.from_tensor_slices(X).batch(batch_size).prefetch(tf.data.AUTOTUNE)
    for batch in dataset:
        recon = model.predict(batch, verbose=0)
        batch_scores = np.mean((batch.numpy() - recon) ** 2, axis=1)
        scores.append(batch_scores)
    scores = np.concatenate(scores)
    np.save(output_file, scores)
    return scores

# Step 4: Batch-Specific GNN
class GNN(torch.nn.Module):
    def __init__(self, in_channels):
        super(GNN, self).__init__()
        self.conv1 = GCNConv(in_channels, 64)
        self.conv2 = GCNConv(64, 32)
        self.out = torch.nn.Linear(32, 1)

    def forward(self, x, edge_index):
        x = self.conv1(x, edge_index).relu()
        x = self.conv2(x, edge_index).relu()
        return self.out(x)

gnn = GNN(X_train_clean.shape[1])
optimizer = torch.optim.Adam(gnn.parameters(), lr=0.01)
criterion = torch.nn.MSELoss()
for epoch in range(5):
    gnn.train()
    batch_size = 40000
    total_loss = 0
    for i in range(0, len(X_train_clean), batch_size):
        X_batch = X_train_clean[i:i+batch_size]
        gnn_data_batch = build_gnn_data_batch(X_batch)
        optimizer.zero_grad()
        out = gnn(gnn_data_batch.x, gnn_data_batch.edge_index)
        loss = criterion(out, gnn_data_batch.x[:, :1])
        loss.backward()
        optimizer.step()
        total_loss += loss.item()
    print(f"Epoch {epoch+1}, Avg Batch Loss: {total_loss / (len(X_train_clean) // batch_size):.4f}")
torch.save(gnn.state_dict(), '/content/drive/My Drive/AI_Security_Project/gnn_fgsm.pth')

def build_gnn_data_batch(X_batch):
    from sklearn.neighbors import kneighbors_graph
    adj = kneighbors_graph(X_batch, n_neighbors=3, mode='connectivity', include_self=False)
    edge_index = torch.tensor(np.array(csr_matrix(adj).nonzero()), dtype=torch.long)
    return Data(x=torch.tensor(X_batch, dtype=torch.float), edge_index=edge_index)

def get_gnn_scores(X, gnn, batch_size=40000, output_file='gnn_scores.npy'):
    gnn.eval()
    scores = []
    for i in range(0, len(X), batch_size):
        X_batch = X[i:i+batch_size]
        gnn_data_batch = build_gnn_data_batch(X_batch)
        with torch.no_grad():
            batch_scores = gnn(gnn_data_batch.x, gnn_data_batch.edge_index).numpy().flatten()
        scores.append(batch_scores)
    scores = np.concatenate(scores)
    np.save(output_file, scores)
    return scores

# Step 5: Adversarial Feature Augmentation (AFA) with ART
X_subset, _, y_subset, _ = train_test_split(X_train_clean, y_full, train_size=10000, stratify=y_full, random_state=42)
scaler = StandardScaler()
X_subset_scaled = scaler.fit_transform(X_subset)

surrogate_model = LogisticRegression(max_iter=1000, solver='lbfgs')
surrogate_model.fit(X_subset_scaled, y_subset)

art_classifier = SklearnClassifier(model=surrogate_model)
fgsm_aug = FastGradientMethod(estimator=art_classifier, eps=0.1)
X_train_clean_scaled = scaler.transform(X_train_clean[:10000])
X_aug_fgsm = fgsm_aug.generate(X_train_clean_scaled)
X_augmented = np.vstack([X_train_clean[:10000], scaler.inverse_transform(X_aug_fgsm)])

# Step 6: FGSM Beast Detector with Incremental Learning
class AdaptiveWeightLearner(tf.keras.Model):
    def __init__(self):
        super(AdaptiveWeightLearner, self).__init__()
        self.dense1 = layers.Dense(16, activation='relu')
        self.dense2 = layers.Dense(3, activation='softmax')  # Weights for DDAE, GNN, Iso

    def call(self, inputs):
        x = self.dense1(inputs)
        return self.dense2(x)

adaptive_learner = AdaptiveWeightLearner()
adaptive_learner.build(input_shape=(None, 3))
weight_file = '/content/drive/My Drive/AI_Security_Project/adaptive_weights_fgsm.h5'

def fgsm_beast_detector(X_clean, X_poisoned, incremental=True):
    print("Training FGSM Beast Detector...")

    # DDAE Scores
    ddae_clean_scores = get_ddae_scores(X_clean, ddae, output_file='/content/ddae_clean_fgsm.npy')
    ddae_poisoned_scores = get_ddae_scores(X_poisoned, ddae, output_file='/content/ddae_poisoned_fgsm.npy')

    # GNN Scores
    gnn_clean_scores = get_gnn_scores(X_clean, gnn, output_file='/content/gnn_clean_fgsm.npy')
    gnn_poisoned_scores = get_gnn_scores(X_poisoned, gnn, output_file='/content/gnn_poisoned_fgsm.npy')

    # Isolation Forest
    iso_forest = IsolationForest(contamination=0.5, random_state=42, n_estimators=100)
    iso_forest.fit(np.vstack([X_clean[:50000], X_augmented]))
    iso_clean_scores = -iso_forest.decision_function(X_clean)
    iso_poisoned_scores = -iso_forest.decision_function(X_poisoned)
    np.save('/content/iso_clean_fgsm.npy', iso_clean_scores)
    np.save('/content/iso_poisoned_fgsm.npy', iso_poisoned_scores)

    # Ensemble with LightGBM - Incremental Training
    batch_size = 100000
    X_ensemble_clean = np.vstack([ddae_clean_scores, gnn_clean_scores, iso_clean_scores]).T
    X_ensemble_poisoned = np.vstack([ddae_poisoned_scores, gnn_poisoned_scores, iso_poisoned_scores]).T
    X_ensemble = np.vstack([X_ensemble_clean, X_ensemble_poisoned])
    y_ensemble = np.concatenate([np.zeros(len(X_clean)), np.ones(len(X_poisoned))])

    # Shuffle for balanced chunks
    indices = np.random.permutation(len(X_ensemble))
    X_ensemble_shuffled = X_ensemble[indices]
    y_ensemble_shuffled = y_ensemble[indices]

    # Load or initialize LightGBM
    lgb_file = '/content/drive/My Drive/AI_Security_Project/beast_detector_fgsm.pkl'
    if os.path.exists(lgb_file) and incremental:
        with open(lgb_file, 'rb') as f:
            lgb_model = pickle.load(f)
    else:
        lgb_model = lgb.LGBMClassifier(n_estimators=50, learning_rate=0.05)

    # Adaptive weighting
    if not os.path.exists(weight_file):
        adaptive_learner.compile(optimizer='adam', loss='categorical_crossentropy')
        weights = np.ones((len(X_ensemble), 3)) / 3  # Initial equal weights
        adaptive_learner.fit(X_ensemble, weights, epochs=5, batch_size=10000, verbose=1)
    weights = adaptive_learner.predict(X_ensemble, batch_size=10000)
    adaptive_learner.save_weights(weight_file)

    # Incremental Training
    for i in range(0, len(X_ensemble_shuffled), batch_size):
        X_chunk = X_ensemble_shuffled[i:i+batch_size]
        y_chunk = y_ensemble_shuffled[i:i+batch_size]
        if i == 0 or not incremental or not os.path.exists(lgb_file):
            lgb_model.fit(X_chunk, y_chunk)
        else:
            lgb_model.fit(X_chunk, y_chunk, init_model=lgb_model)

    # Final Predictions with Unshuffled Data
    clean_pred = lgb_model.predict_proba(X_ensemble_clean)[:, 1]
    poisoned_pred = lgb_model.predict_proba(X_ensemble_poisoned)[:, 1]

    clean_anomaly_rate = np.mean(clean_pred > 0.5) * 100
    poisoned_anomaly_rate = np.mean(poisoned_pred > 0.5) * 100

    print("FGSM Beast Detector Results:")
    print(f"Clean data anomaly rate: {clean_anomaly_rate:.2f}%")
    print(f"Poisoned data anomaly rate: {poisoned_anomaly_rate:.2f}%")
    print(f"Detection: {'Poisoned' if poisoned_anomaly_rate > 5 else 'Clean'}")
    print(f"Estimated poisoning percentage: {poisoned_anomaly_rate:.2f}%")

    auc = roc_auc_score(np.concatenate([np.zeros(len(X_clean)), np.ones(len(X_poisoned))]), np.concatenate([clean_pred, poisoned_pred]))
    print(f"AUC Score: {auc:.4f}")

    # Clean up
    for f in ['ddae_clean_fgsm.npy', 'ddae_poisoned_fgsm.npy', 'gnn_clean_fgsm.npy', 'gnn_poisoned_fgsm.npy', 'iso_clean_fgsm.npy', 'iso_poisoned_fgsm.npy']:
        os.remove(f'/content/{f}')

    return lgb_model, iso_forest, ddae, gnn

# Step 7: Train and Save FGSM Detector
detector_fgsm, iso_fgsm, ddae_fgsm, gnn_fgsm = fgsm_beast_detector(X_train_clean, X_train_fgsm)
with open('/content/drive/My Drive/AI_Security_Project/beast_detector_fgsm.pkl', 'wb') as f:
    pickle.dump(detector_fgsm, f)
print("FGSM Beast Detector saved to Drive.")

BEASTEST - PGD - DETECTOR

In [ ]:
# Step 1: Install Libraries
!pip install scikit-learn numpy pandas tensorflow==2.15.0 adversarial-robustness-toolbox lightgbm
!pip install torch==2.5.1 -f https://download.pytorch.org/whl/torch_stable.html
!pip install torch-geometric

import numpy as np
import tensorflow as tf
from tensorflow.keras import layers, Model
from sklearn.ensemble import IsolationForest
from sklearn.metrics import roc_auc_score
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from art.attacks.evasion import ProjectedGradientDescent
from art.estimators.classification import SklearnClassifier
import torch
from torch_geometric.nn import GCNConv
from torch_geometric.data import Data
from scipy.sparse import csr_matrix
import lightgbm as lgb
from google.colab import drive
import pickle
import os

drive.mount('/content/drive')

# Step 2: Load Data (PGD Only)
X_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/X_train_clean.npy')
X_train_pgd = np.load('/content/drive/My Drive/AI_Security_Project/X_train_pgd.npy')
y_full = np.load('/content/drive/My Drive/AI_Security_Project/y_train_clean.npy')

# Step 3: Deep Denoising Autoencoder (DDAE)
def build_ddae(input_dim):
    inputs = layers.Input(shape=(input_dim,))
    enc = layers.Dense(128, activation='relu')(inputs)
    enc = layers.Dense(64, activation='relu')(enc)
    latent = layers.Dense(32, activation='relu')(enc)
    dec = layers.Dense(64, activation='relu')(latent)
    dec = layers.Dense(128, activation='relu')(dec)
    outputs = layers.Dense(input_dim, activation='linear')(dec)
    model = Model(inputs, outputs)
    model.compile(optimizer='adam', loss='mse')
    return model

ddae = build_ddae(X_train_clean.shape[1])
dataset = tf.data.Dataset.from_tensor_slices((X_train_clean, X_train_clean)).batch(40000).prefetch(tf.data.AUTOTUNE)
ddae.fit(dataset, epochs=5, verbose=1)
with open('/content/drive/My Drive/AI_Security_Project/ddae_pgd.pkl', 'wb') as f:
    pickle.dump(ddae, f)

def get_ddae_scores(X, model, batch_size=40000, output_file='ddae_scores.npy'):
    scores = []
    dataset = tf.data.Dataset.from_tensor_slices(X).batch(batch_size).prefetch(tf.data.AUTOTUNE)
    for batch in dataset:
        recon = model.predict(batch, verbose=0)
        batch_scores = np.mean((batch.numpy() - recon) ** 2, axis=1)
        scores.append(batch_scores)
    scores = np.concatenate(scores)
    np.save(output_file, scores)
    return scores

# Step 4: Batch-Specific GNN
class GNN(torch.nn.Module):
    def __init__(self, in_channels):
        super(GNN, self).__init__()
        self.conv1 = GCNConv(in_channels, 64)
        self.conv2 = GCNConv(64, 32)
        self.out = torch.nn.Linear(32, 1)

    def forward(self, x, edge_index):
        x = self.conv1(x, edge_index).relu()
        x = self.conv2(x, edge_index).relu()
        return self.out(x)

gnn = GNN(X_train_clean.shape[1])
optimizer = torch.optim.Adam(gnn.parameters(), lr=0.01)
criterion = torch.nn.MSELoss()
for epoch in range(5):
    gnn.train()
    batch_size = 40000
    total_loss = 0
    for i in range(0, len(X_train_clean), batch_size):
        X_batch = X_train_clean[i:i+batch_size]
        gnn_data_batch = build_gnn_data_batch(X_batch)
        optimizer.zero_grad()
        out = gnn(gnn_data_batch.x, gnn_data_batch.edge_index)
        loss = criterion(out, gnn_data_batch.x[:, :1])
        loss.backward()
        optimizer.step()
        total_loss += loss.item()
    print(f"Epoch {epoch+1}, Avg Batch Loss: {total_loss / (len(X_train_clean) // batch_size):.4f}")
torch.save(gnn.state_dict(), '/content/drive/My Drive/AI_Security_Project/gnn_pgd.pth')

def build_gnn_data_batch(X_batch):
    from sklearn.neighbors import kneighbors_graph
    adj = kneighbors_graph(X_batch, n_neighbors=3, mode='connectivity', include_self=False)
    edge_index = torch.tensor(np.array(csr_matrix(adj).nonzero()), dtype=torch.long)
    return Data(x=torch.tensor(X_batch, dtype=torch.float), edge_index=edge_index)

def get_gnn_scores(X, gnn, batch_size=40000, output_file='gnn_scores.npy'):
    gnn.eval()
    scores = []
    for i in range(0, len(X), batch_size):
        X_batch = X[i:i+batch_size]
        gnn_data_batch = build_gnn_data_batch(X_batch)
        with torch.no_grad():
            batch_scores = gnn(gnn_data_batch.x, gnn_data_batch.edge_index).numpy().flatten()
        scores.append(batch_scores)
    scores = np.concatenate(scores)
    np.save(output_file, scores)
    return scores

# Step 5: Adversarial Feature Augmentation (AFA) with ART
X_subset, _, y_subset, _ = train_test_split(X_train_clean, y_full, train_size=10000, stratify=y_full, random_state=42)
scaler = StandardScaler()
X_subset_scaled = scaler.fit_transform(X_subset)

surrogate_model = LogisticRegression(max_iter=1000, solver='lbfgs')
surrogate_model.fit(X_subset_scaled, y_subset)

art_classifier = SklearnClassifier(model=surrogate_model)
pgd_aug = ProjectedGradientDescent(estimator=art_classifier, eps=0.1, max_iter=5)
X_train_clean_scaled = scaler.transform(X_train_clean[:10000])
X_aug_pgd = pgd_aug.generate(X_train_clean_scaled)
X_augmented = np.vstack([X_train_clean[:10000], scaler.inverse_transform(X_aug_pgd)])

# Step 6: PGD Beast Detector with Incremental Learning
class AdaptiveWeightLearner(tf.keras.Model):
    def __init__(self):
        super(AdaptiveWeightLearner, self).__init__()
        self.dense1 = layers.Dense(16, activation='relu')
        self.dense2 = layers.Dense(3, activation='softmax')

    def call(self, inputs):
        x = self.dense1(inputs)
        return self.dense2(x)

adaptive_learner = AdaptiveWeightLearner()
adaptive_learner.build(input_shape=(None, 3))
weight_file = '/content/drive/My Drive/AI_Security_Project/adaptive_weights_pgd.h5'

def pgd_beast_detector(X_clean, X_poisoned, incremental=True):
    print("Training PGD Beast Detector...")

    # DDAE Scores
    ddae_clean_scores = get_ddae_scores(X_clean, ddae, output_file='/content/ddae_clean_pgd.npy')
    ddae_poisoned_scores = get_ddae_scores(X_poisoned, ddae, output_file='/content/ddae_poisoned_pgd.npy')

    # GNN Scores
    gnn_clean_scores = get_gnn_scores(X_clean, gnn, output_file='/content/gnn_clean_pgd.npy')
    gnn_poisoned_scores = get_gnn_scores(X_poisoned, gnn, output_file='/content/gnn_poisoned_pgd.npy')

    # Isolation Forest
    iso_forest = IsolationForest(contamination=0.5, random_state=42, n_estimators=100)
    iso_forest.fit(np.vstack([X_clean[:50000], X_augmented]))
    iso_clean_scores = -iso_forest.decision_function(X_clean)
    iso_poisoned_scores = -iso_forest.decision_function(X_poisoned)
    np.save('/content/iso_clean_pgd.npy', iso_clean_scores)
    np.save('/content/iso_poisoned_pgd.npy', iso_poisoned_scores)

    # Ensemble with LightGBM - Incremental Training
    batch_size = 100000
    X_ensemble_clean = np.vstack([ddae_clean_scores, gnn_clean_scores, iso_clean_scores]).T
    X_ensemble_poisoned = np.vstack([ddae_poisoned_scores, gnn_poisoned_scores, iso_poisoned_scores]).T
    X_ensemble = np.vstack([X_ensemble_clean, X_ensemble_poisoned])
    y_ensemble = np.concatenate([np.zeros(len(X_clean)), np.ones(len(X_poisoned))])

    # Shuffle for balanced chunks
    indices = np.random.permutation(len(X_ensemble))
    X_ensemble_shuffled = X_ensemble[indices]
    y_ensemble_shuffled = y_ensemble[indices]

    # Load or initialize LightGBM
    lgb_file = '/content/drive/My Drive/AI_Security_Project/beast_detector_pgd.pkl'
    if os.path.exists(lgb_file) and incremental:
        with open(lgb_file, 'rb') as f:
            lgb_model = pickle.load(f)
    else:
        lgb_model = lgb.LGBMClassifier(n_estimators=50, learning_rate=0.05)

    # Adaptive weighting
    if not os.path.exists(weight_file):
        adaptive_learner.compile(optimizer='adam', loss='categorical_crossentropy')
        weights = np.ones((len(X_ensemble), 3)) / 3
        adaptive_learner.fit(X_ensemble, weights, epochs=5, batch_size=10000, verbose=1)
    weights = adaptive_learner.predict(X_ensemble, batch_size=10000)
    adaptive_learner.save_weights(weight_file)

    # Incremental Training
    for i in range(0, len(X_ensemble_shuffled), batch_size):
        X_chunk = X_ensemble_shuffled[i:i+batch_size]
        y_chunk = y_ensemble_shuffled[i:i+batch_size]
        if i == 0 or not incremental or not os.path.exists(lgb_file):
            lgb_model.fit(X_chunk, y_chunk)
        else:
            lgb_model.fit(X_chunk, y_chunk, init_model=lgb_model)

    # Final Predictions with Unshuffled Data
    clean_pred = lgb_model.predict_proba(X_ensemble_clean)[:, 1]
    poisoned_pred = lgb_model.predict_proba(X_ensemble_poisoned)[:, 1]

    clean_anomaly_rate = np.mean(clean_pred > 0.5) * 100
    poisoned_anomaly_rate = np.mean(poisoned_pred > 0.5) * 100

    print("PGD Beast Detector Results:")
    print(f"Clean data anomaly rate: {clean_anomaly_rate:.2f}%")
    print(f"Poisoned data anomaly rate: {poisoned_anomaly_rate:.2f}%")
    print(f"Detection: {'Poisoned' if poisoned_anomaly_rate > 5 else 'Clean'}")
    print(f"Estimated poisoning percentage: {poisoned_anomaly_rate:.2f}%")

    auc = roc_auc_score(np.concatenate([np.zeros(len(X_clean)), np.ones(len(X_poisoned))]), np.concatenate([clean_pred, poisoned_pred]))
    print(f"AUC Score: {auc:.4f}")

    # Clean up
    for f in ['ddae_clean_pgd.npy', 'ddae_poisoned_pgd.npy', 'gnn_clean_pgd.npy', 'gnn_poisoned_pgd.npy', 'iso_clean_pgd.npy', 'iso_poisoned_pgd.npy']:
        os.remove(f'/content/{f}')

    return lgb_model, iso_forest, ddae, gnn

# Step 7: Train and Save PGD Detector
detector_pgd, iso_pgd, ddae_pgd, gnn_pgd = pgd_beast_detector(X_train_clean, X_train_pgd)
with open('/content/drive/My Drive/AI_Security_Project/beast_detector_pgd.pkl', 'wb') as f:
    pickle.dump(detector_pgd, f)
print("PGD Beast Detector saved to Drive.")

Looking in links: https://download.pytorch.org/whl/torch_stable.html
Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Epoch 1/5
10/10 [==============================] - 16s 1s/step - loss: 314009452544.0000
Epoch 2/5
10/10 [==============================] - 14s 1s/step - loss: 263221198848.0000
Epoch 3/5
10/10 [==============================] - 14s 1s/step - loss: 142316716032.0000
Epoch 4/5
10/10 [==============================] - 15s 2s/step - loss: 60487966720.0000
Epoch 5/5
10/10 [==============================] - 14s 1s/step - loss: 28135057408.0000
Epoch 1, Avg Batch Loss: 386846431232.0000
Epoch 2, Avg Batch Loss: 486160420044.8000
Epoch 3, Avg Batch Loss: 274170627686.4000
Epoch 4, Avg Batch Loss: 275776058982.4000
Epoch 5, Avg Batch Loss: 243434690150.4000


PGD - Random Initializations:   0%|          | 0/1 [00:00<?, ?it/s]

PGD - Iterations:   0%|          | 0/5 [00:00<?, ?it/s]

PGD - Random Initializations:   0%|          | 0/1 [00:00<?, ?it/s]

PGD - Iterations:   0%|          | 0/5 [00:00<?, ?it/s]

...

PGD - Random Initializations:   0%|          | 0/1 [00:00<?, ?it/s]

PGD - Iterations:   0%|          | 0/5 [00:00<?, ?it/s]

Training PGD Beast Detector...
Epoch 1/5
80/80 [==============================] - 1s 4ms/step - loss: 2336614656.0000
Epoch 2/5
80/80 [==============================] - 0s 4ms/step - loss: 624999808.0000
Epoch 3/5
80/80 [==============================] - 0s 4ms/step - loss: 20556366.0000
Epoch 4/5
80/80 [==============================] - 0s 4ms/step - loss: 15019741.0000
Epoch 5/5
80/80 [==============================] - 0s 2ms/step
[LightGBM] [Info] Number of positive: 49779, number of negative: 50221
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000576 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 765
[LightGBM] [Info] Number of data points in the train set: 100000, number of used features: 3
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.497790 -> initscore=-0.008840
[LightGBM] [Info] Start training from score -0.008840
[Light

/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(


PGD Beast Detector Results:
Clean data anomaly rate: 7.38%
Poisoned data anomaly rate: 97.25%
Detection: Poisoned
Estimated poisoning percentage: 97.25%
AUC Score: 0.9906
PGD Beast Detector saved to Drive.


BEASTEST - BACKDOOR - DETECTOR

In [ ]:
# Step 1: Install Libraries
!pip install scikit-learn numpy pandas tensorflow==2.15.0 adversarial-robustness-toolbox lightgbm
!pip install torch==2.5.1 -f https://download.pytorch.org/whl/torch_stable.html
!pip install torch-geometric

import numpy as np
import tensorflow as tf
from tensorflow.keras import layers, Model
from sklearn.ensemble import IsolationForest
from sklearn.metrics import roc_auc_score
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from art.attacks.evasion import FastGradientMethod  # Placeholder, Backdoor doesn’t use ART here
from art.estimators.classification import SklearnClassifier
import torch
from torch_geometric.nn import GCNConv
from torch_geometric.data import Data
from scipy.sparse import csr_matrix
import lightgbm as lgb
from google.colab import drive
import pickle
import os

drive.mount('/content/drive')

# Step 2: Load Data (Backdoor Only)
X_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/X_train_clean.npy')
X_train_backdoor = np.load('/content/drive/My Drive/AI_Security_Project/X_train_backdoor.npy')
y_full = np.load('/content/drive/My Drive/AI_Security_Project/y_train_clean.npy')  # Note: Backdoor may have flipped labels, adjust if needed

# Step 3: Deep Denoising Autoencoder (DDAE)
def build_ddae(input_dim):
    inputs = layers.Input(shape=(input_dim,))
    enc = layers.Dense(128, activation='relu')(inputs)
    enc = layers.Dense(64, activation='relu')(enc)
    latent = layers.Dense(32, activation='relu')(enc)
    dec = layers.Dense(64, activation='relu')(latent)
    dec = layers.Dense(128, activation='relu')(dec)
    outputs = layers.Dense(input_dim, activation='linear')(dec)
    model = Model(inputs, outputs)
    model.compile(optimizer='adam', loss='mse')
    return model

ddae = build_ddae(X_train_clean.shape[1])
dataset = tf.data.Dataset.from_tensor_slices((X_train_clean, X_train_clean)).batch(40000).prefetch(tf.data.AUTOTUNE)
ddae.fit(dataset, epochs=5, verbose=1)
with open('/content/drive/My Drive/AI_Security_Project/ddae_backdoor.pkl', 'wb') as f:
    pickle.dump(ddae, f)

def get_ddae_scores(X, model, batch_size=40000, output_file='ddae_scores.npy'):
    scores = []
    dataset = tf.data.Dataset.from_tensor_slices(X).batch(batch_size).prefetch(tf.data.AUTOTUNE)
    for batch in dataset:
        recon = model.predict(batch, verbose=0)
        batch_scores = np.mean((batch.numpy() - recon) ** 2, axis=1)
        scores.append(batch_scores)
    scores = np.concatenate(scores)
    np.save(output_file, scores)
    return scores

# Step 4: Batch-Specific GNN
class GNN(torch.nn.Module):
    def __init__(self, in_channels):
        super(GNN, self).__init__()
        self.conv1 = GCNConv(in_channels, 64)
        self.conv2 = GCNConv(64, 32)
        self.out = torch.nn.Linear(32, 1)

    def forward(self, x, edge_index):
        x = self.conv1(x, edge_index).relu()
        x = self.conv2(x, edge_index).relu()
        return self.out(x)

gnn = GNN(X_train_clean.shape[1])
optimizer = torch.optim.Adam(gnn.parameters(), lr=0.01)
criterion = torch.nn.MSELoss()
for epoch in range(5):
    gnn.train()
    batch_size = 40000
    total_loss = 0
    for i in range(0, len(X_train_clean), batch_size):
        X_batch = X_train_clean[i:i+batch_size]
        gnn_data_batch = build_gnn_data_batch(X_batch)
        optimizer.zero_grad()
        out = gnn(gnn_data_batch.x, gnn_data_batch.edge_index)
        loss = criterion(out, gnn_data_batch.x[:, :1])
        loss.backward()
        optimizer.step()
        total_loss += loss.item()
    print(f"Epoch {epoch+1}, Avg Batch Loss: {total_loss / (len(X_train_clean) // batch_size):.4f}")
torch.save(gnn.state_dict(), '/content/drive/My Drive/AI_Security_Project/gnn_backdoor.pth')

def build_gnn_data_batch(X_batch):
    from sklearn.neighbors import kneighbors_graph
    adj = kneighbors_graph(X_batch, n_neighbors=3, mode='connectivity', include_self=False)
    edge_index = torch.tensor(np.array(csr_matrix(adj).nonzero()), dtype=torch.long)
    return Data(x=torch.tensor(X_batch, dtype=torch.float), edge_index=edge_index)

def get_gnn_scores(X, gnn, batch_size=40000, output_file='gnn_scores.npy'):
    gnn.eval()
    scores = []
    for i in range(0, len(X), batch_size):
        X_batch = X[i:i+batch_size]
        gnn_data_batch = build_gnn_data_batch(X_batch)
        with torch.no_grad():
            batch_scores = gnn(gnn_data_batch.x, gnn_data_batch.edge_index).numpy().flatten()
        scores.append(batch_scores)
    scores = np.concatenate(scores)
    np.save(output_file, scores)
    return scores

# Step 5: Adversarial Feature Augmentation (AFA) with ART (Using FGSM as Placeholder for Backdoor)
X_subset, _, y_subset, _ = train_test_split(X_train_clean, y_full, train_size=10000, stratify=y_full, random_state=42)
scaler = StandardScaler()
X_subset_scaled = scaler.fit_transform(X_subset)

surrogate_model = LogisticRegression(max_iter=1000, solver='lbfgs')
surrogate_model.fit(X_subset_scaled, y_subset)

art_classifier = SklearnClassifier(model=surrogate_model)
fgsm_aug = FastGradientMethod(estimator=art_classifier, eps=0.1)  # Placeholder, Backdoor doesn’t need this
X_train_clean_scaled = scaler.transform(X_train_clean[:10000])
X_aug_fgsm = fgsm_aug.generate(X_train_clean_scaled)
X_augmented = np.vstack([X_train_clean[:10000], scaler.inverse_transform(X_aug_fgsm)])

# Step 6: Backdoor Beast Detector with Incremental Learning
class AdaptiveWeightLearner(tf.keras.Model):
    def __init__(self):
        super(AdaptiveWeightLearner, self).__init__()
        self.dense1 = layers.Dense(16, activation='relu')
        self.dense2 = layers.Dense(3, activation='softmax')

    def call(self, inputs):
        x = self.dense1(inputs)
        return self.dense2(x)

adaptive_learner = AdaptiveWeightLearner()
adaptive_learner.build(input_shape=(None, 3))
weight_file = '/content/drive/My Drive/AI_Security_Project/adaptive_weights_backdoor.h5'

def backdoor_beast_detector(X_clean, X_poisoned, incremental=True):
    print("Training Backdoor Beast Detector...")

    # DDAE Scores
    ddae_clean_scores = get_ddae_scores(X_clean, ddae, output_file='/content/ddae_clean_backdoor.npy')
    ddae_poisoned_scores = get_ddae_scores(X_poisoned, ddae, output_file='/content/ddae_poisoned_backdoor.npy')

    # GNN Scores
    gnn_clean_scores = get_gnn_scores(X_clean, gnn, output_file='/content/gnn_clean_backdoor.npy')
    gnn_poisoned_scores = get_gnn_scores(X_poisoned, gnn, output_file='/content/gnn_poisoned_backdoor.npy')

    # Isolation Forest
    iso_forest = IsolationForest(contamination=0.5, random_state=42, n_estimators=100)
    iso_forest.fit(np.vstack([X_clean[:50000], X_augmented]))
    iso_clean_scores = -iso_forest.decision_function(X_clean)
    iso_poisoned_scores = -iso_forest.decision_function(X_poisoned)
    np.save('/content/iso_clean_backdoor.npy', iso_clean_scores)
    np.save('/content/iso_poisoned_backdoor.npy', iso_poisoned_scores)

    # Ensemble with LightGBM - Incremental Training
    batch_size = 100000
    X_ensemble_clean = np.vstack([ddae_clean_scores, gnn_clean_scores, iso_clean_scores]).T
    X_ensemble_poisoned = np.vstack([ddae_poisoned_scores, gnn_poisoned_scores, iso_poisoned_scores]).T
    X_ensemble = np.vstack([X_ensemble_clean, X_ensemble_poisoned])
    y_ensemble = np.concatenate([np.zeros(len(X_clean)), np.ones(len(X_poisoned))])

    # Shuffle for balanced chunks
    indices = np.random.permutation(len(X_ensemble))
    X_ensemble_shuffled = X_ensemble[indices]
    y_ensemble_shuffled = y_ensemble[indices]

    # Load or initialize LightGBM
    lgb_file = '/content/drive/My Drive/AI_Security_Project/beast_detector_backdoor.pkl'
    if os.path.exists(lgb_file) and incremental:
        with open(lgb_file, 'rb') as f:
            lgb_model = pickle.load(f)
    else:
        lgb_model = lgb.LGBMClassifier(n_estimators=50, learning_rate=0.05)

    # Adaptive weighting
    if not os.path.exists(weight_file):
        adaptive_learner.compile(optimizer='adam', loss='categorical_crossentropy')
        weights = np.ones((len(X_ensemble), 3)) / 3
        adaptive_learner.fit(X_ensemble, weights, epochs=5, batch_size=10000, verbose=1)
    weights = adaptive_learner.predict(X_ensemble, batch_size=10000)
    adaptive_learner.save_weights(weight_file)

    # Incremental Training
    for i in range(0, len(X_ensemble_shuffled), batch_size):
        X_chunk = X_ensemble_shuffled[i:i+batch_size]
        y_chunk = y_ensemble_shuffled[i:i+batch_size]
        if i == 0 or not incremental or not os.path.exists(lgb_file):
            lgb_model.fit(X_chunk, y_chunk)
        else:
            lgb_model.fit(X_chunk, y_chunk, init_model=lgb_model)

    # Final Predictions with Unshuffled Data
    clean_pred = lgb_model.predict_proba(X_ensemble_clean)[:, 1]
    poisoned_pred = lgb_model.predict_proba(X_ensemble_poisoned)[:, 1]

    clean_anomaly_rate = np.mean(clean_pred > 0.5) * 100
    poisoned_anomaly_rate = np.mean(poisoned_pred > 0.5) * 100

    print("Backdoor Beast Detector Results:")
    print(f"Clean data anomaly rate: {clean_anomaly_rate:.2f}%")
    print(f"Poisoned data anomaly rate: {poisoned_anomaly_rate:.2f}%")
    print(f"Detection: {'Poisoned' if poisoned_anomaly_rate > 5 else 'Clean'}")
    print(f"Estimated poisoning percentage: {poisoned_anomaly_rate:.2f}%")

    auc = roc_auc_score(np.concatenate([np.zeros(len(X_clean)), np.ones(len(X_poisoned))]), np.concatenate([clean_pred, poisoned_pred]))
    print(f"AUC Score: {auc:.4f}")

    # Clean up
    for f in ['ddae_clean_backdoor.npy', 'ddae_poisoned_backdoor.npy', 'gnn_clean_backdoor.npy', 'gnn_poisoned_backdoor.npy', 'iso_clean_backdoor.npy', 'iso_poisoned_backdoor.npy']:
        os.remove(f'/content/{f}')

    return lgb_model, iso_forest, ddae, gnn

# Step 7: Train and Save Backdoor Detector
detector_backdoor, iso_backdoor, ddae_backdoor, gnn_backdoor = backdoor_beast_detector(X_train_clean, X_train_backdoor)
with open('/content/drive/My Drive/AI_Security_Project/beast_detector_backdoor.pkl', 'wb') as f:
    pickle.dump(detector_backdoor, f)
print("Backdoor Beast Detector saved to Drive.")

Looking in links: https://download.pytorch.org/whl/torch_stable.html
Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Epoch 1/5
10/10 [==============================] - 15s 1s/step - loss: 314147340288.0000
Epoch 2/5
10/10 [==============================] - 14s 1s/step - loss: 257430913024.0000
Epoch 3/5
10/10 [==============================] - 14s 1s/step - loss: 133886976000.0000
Epoch 4/5
10/10 [==============================] - 15s 1s/step - loss: 54552997888.0000
Epoch 5/5
10/10 [==============================] - 14s 1s/step - loss: 26959491072.0000
Epoch 1, Avg Batch Loss: 467917017088.0000
Epoch 2, Avg Batch Loss: 307663648358.4000
Epoch 3, Avg Batch Loss: 252965630771.2000
Epoch 4, Avg Batch Loss: 242185272934.4000
Epoch 5, Avg Batch Loss: 252268341657.6000
Training Backdoor Beast Detector...
Epoch 1/5
80/80 [==============================] - 1s 4ms/step - loss: 4559361024.0000
Epoch 2/5
80/80 [====

/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(


Backdoor Beast Detector Results:
Clean data anomaly rate: 56.09%
Poisoned data anomaly rate: 62.67%
Detection: Poisoned
Estimated poisoning percentage: 62.67%
AUC Score: 0.5554
Backdoor Beast Detector saved to Drive.


Code: FGSM Beast Corrector (Split Across Scripts)
Script 1: QTP and HAI Training/Saving

In [ ]:
# Step 1: Install Libraries
!pip install tensorflow==2.15.0 numpy tensorly scikit-learn

import numpy as np
import tensorflow as tf
from tensorflow.keras import layers, Model
import tensorly as tl
from sklearn.preprocessing import StandardScaler
from google.colab import drive
import pickle
import os

drive.mount('/content/drive')

# Step 2: Load Data
X_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/X_train_clean.npy')
X_train_fgsm = np.load('/content/drive/My Drive/AI_Security_Project/X_train_fgsm.npy')
y_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/y_train_clean.npy')

# Step 3: Quantum Tensor Purification (QTP)
class QTP(Model):
    def __init__(self, input_dim, latent_dim=32):
        super(QTP, self).__init__()
        self.encoder = tf.keras.Sequential([
            layers.Dense(128, activation='relu'),
            layers.Dense(64, activation='relu'),
            layers.Dense(latent_dim, activation='tanh')
        ])
        self.decoder = tf.keras.Sequential([
            layers.Dense(64, activation='relu'),
            layers.Dense(128, activation='relu'),
            layers.Dense(input_dim, activation='linear')
        ])

    def call(self, inputs):
        latent = self.encoder(inputs)
        latent_diffused = latent + tf.random.normal(tf.shape(latent), stddev=0.01, dtype=tf.float32)
        return self.decoder(latent_diffused)

qtp_file = '/content/drive/My Drive/AI_Security_Project/qtp_fgsm.pkl'
if os.path.exists(qtp_file):
    with open(qtp_file, 'rb') as f:
        qtp = pickle.load(f)
    print(f"Loaded pre-trained QTP from {qtp_file}")
else:
    qtp = QTP(X_train_clean.shape[1])
    scaler = StandardScaler()
    X_train_clean_scaled = scaler.fit_transform(X_train_clean)
    dataset = tf.data.Dataset.from_tensor_slices(X_train_clean_scaled).map(lambda x: tf.cast(x, tf.float32)).batch(40000).prefetch(tf.data.AUTOTUNE)
    optimizer = tf.keras.optimizers.Adam(learning_rate=0.001)
    for epoch in range(5):
        total_loss = 0
        for batch in dataset:
            with tf.GradientTape() as tape:
                recon = qtp(batch)
                loss = tf.reduce_mean(tf.square(recon - batch)) + 0.1 * tf.reduce_mean(tf.abs(recon))
            grads = tape.gradient(loss, qtp.trainable_variables)
            optimizer.apply_gradients(zip(grads, qtp.trainable_variables))
            total_loss += loss.numpy()
        print(f"QTP Epoch {epoch+1}, Loss: {total_loss:.4f}")
    with open(qtp_file, 'wb') as f:
        pickle.dump(qtp, f)
    print(f"QTP model saved to {qtp_file}")

# Step 4: Hyperdimensional Anomaly Isolator (HAI)
def hyperdimensional_encode(X, dim=10000):
    from sklearn.random_projection import GaussianRandomProjection
    projector = GaussianRandomProjection(n_components=dim, random_state=42)
    X_hd = projector.fit_transform(X)
    return X_hd / np.linalg.norm(X_hd, axis=1, keepdims=True)

X_clean_hd = hyperdimensional_encode(X_train_clean)
X_fgsm_hd = hyperdimensional_encode(X_train_fgsm)
np.save('/content/drive/My Drive/AI_Security_Project/hai_clean_fgsm.npy', X_clean_hd)
np.save('/content/drive/My Drive/AI_Security_Project/hai_poisoned_fgsm.npy', X_fgsm_hd)
print(f"HAI encodings saved to Drive: hai_clean_fgsm.npy, hai_poisoned_fgsm.npy")

# Cleanup
del X_train_clean, X_train_fgsm, y_train_clean, qtp, X_clean_hd, X_fgsm_hd
if 'scaler' in locals():
    del scaler
if 'dataset' in locals():
    del dataset
tf.keras.backend.clear_session()
print("QTP and HAI training completed, RAM cleared. Files safe in Google Drive.")

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 475.3/475.3 MB 1.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.4/7.4 MB 30.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 39.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 26.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.5/5.5 MB 30.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 442.0/442.0 kB 22.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.4/78.4 kB 4.9 MB/s eta 0:00:00
  Attempting uninstall: wrapt
    Found existing installation: wrapt 1.17.2
    Uninstalling wrapt-1.17.2:
      Successfully uninstalled wrapt-1.17.2
  Attempting uninstall: ml-dtypes
    Found existing installation: ml-dtypes 0.4.1
    Uninstalling ml-dtypes-0.4.1:
      Successfully uninstalled ml-dtypes-0.4.1
  Attempting uninstall: keras
    Found existing installation: keras 3.8.0
    Uninstalling keras-3.8.0:
      Successfully uninstalled ke

/usr/local/lib/python3.11/dist-packages/sklearn/random_projection.py:411: DataDimensionalityWarning: The number of components is higher than the number of features: n_features < n_components (530 < 10000).The dimensionality of the problem will not be reduced.
  warnings.warn(


Script 2: NSFE and ARE with Incremental Learning

In [ ]:
# Step 1: Install Libraries
!pip install tensorflow==2.15.0 numpy xgboost lightgbm sklearn torch

import numpy as np
import tensorflow as tf
from tensorflow.keras import layers, Model
import xgboost as xgb
import lightgbm as lgb
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import accuracy_score
from google.colab import drive
import pickle
import os

drive.mount('/content/drive')

# Step 2: Load Data and Precomputed Results
X_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/X_train_clean.npy')
X_train_fgsm = np.load('/content/drive/My Drive/AI_Security_Project/X_train_fgsm.npy')
y_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/y_train_clean.npy')
X_test = np.load('/content/drive/My Drive/AI_Security_Project/X_test.npy')
y_test = np.load('/content/drive/My Drive/AI_Security_Project/y_test.npy')
X_clean_hd = np.load('/content/drive/My Drive/AI_Security_Project/hai_clean_fgsm.npy')
X_fgsm_hd = np.load('/content/drive/My Drive/AI_Security_Project/hai_poisoned_fgsm.npy')

# Step 3: Neuro-Symbolic Feature Enforcer (NSFE)
class NSFE(Model):
    def __init__(self, input_dim):
        super(NSFE, self).__init__()
        self.dense = layers.Dense(input_dim, activation='relu')
        self.rules = tf.Variable(tf.random.uniform((input_dim, 2)), trainable=True)  # Min/max bounds per feature

    def call(self, inputs):
        x = self.dense(inputs)
        return tf.clip_by_value(x, self.rules[:, 0], self.rules[:, 1])

nsfe_file = '/content/drive/My Drive/AI_Security_Project/nsfe_fgsm.pkl'
if os.path.exists(nsfe_file):
    with open(nsfe_file, 'rb') as f:
        nsfe = pickle.load(f)
else:
    nsfe = NSFE(X_train_clean.shape[1])
    scaler = StandardScaler()
    X_train_clean_scaled = scaler.fit_transform(X_train_clean)
    dataset = tf.data.Dataset.from_tensor_slices(X_train_clean_scaled).batch(40000).prefetch(tf.data.AUTOTUNE)
    optimizer = tf.keras.optimizers.Adam(learning_rate=0.001)
    for epoch in range(5):
        total_loss = 0
        for batch in dataset:
            with tf.GradientTape() as tape:
                corrected = nsfe(batch)
                loss = tf.reduce_mean(tf.square(corrected - batch))
            grads = tape.gradient(loss, nsfe.trainable_variables)
            optimizer.apply_gradients(zip(grads, nsfe.trainable_variables))
            total_loss += loss.numpy()
        print(f"NSFE Epoch {epoch+1}, Loss: {total_loss:.4f}")
    with open(nsfe_file, 'wb') as f:
        pickle.dump(nsfe, f)
    print(f"NSFE model saved to {nsfe_file}")

# Step 4: Adversarial Retraining Engine (ARE)
def adversarial_retrain(X_corrected, y, X_test, y_test):
    model = xgb.XGBClassifier()
    model.fit(X_corrected, y)
    y_pred = model.predict(X_test)
    accuracy = accuracy_score(y_test, y_pred)
    print(f"ARE Initial Accuracy: {accuracy*100:.2f}%")
    return model

are_file = '/content/drive/My Drive/AI_Security_Project/are_fgsm.pkl'
if os.path.exists(are_file):
    with open(are_file, 'rb') as f:
        are_model = pickle.load(f)
else:
    are_model = adversarial_retrain(X_train_clean, y_train_clean, X_test, y_test)
    with open(are_file, 'wb') as f:
        pickle.dump(are_model, f)

# Step 5: Incremental Meta-Learning Core (IMLC)
class IMLC(Model):
    def __init__(self):
        super(IMLC, self).__init__()
        self.meta = layers.Dense(32, activation='relu')
        self.out = layers.Dense(3, activation='softmax')  # Weights for purification components

    def call(self, inputs):
        x = self.meta(inputs)
        return self.out(x)

imlc_file = '/content/drive/My Drive/AI_Security_Project/imlc_fgsm.h5'
if os.path.exists(imlc_file):
    imlc = IMLC()
    imlc.load_weights(imlc_file)
else:
    imlc = IMLC()

# Cleanup
del X_train_clean, X_train_fgsm, y_train_clean, X_test, y_test, X_clean_hd, X_fgsm_hd, nsfe, are_model
if 'scaler' in locals():
    del scaler
if 'dataset' in locals():
    del dataset
tf.keras.backend.clear_session()
print("NSFE, ARE, and IMLC setup completed, RAM cleared. Files safe in Google Drive.")

Script 3: Full FGSM Beast Corrector with Incremental Learning

In [ ]:
# Step 1: Install Libraries
!pip install tensorflow==2.15.0 numpy xgboost lightgbm sklearn torch

import numpy as np
import tensorflow as tf
import xgboost as xgb
import lightgbm as lgb
from sklearn.metrics import accuracy_score
from google.colab import drive
import pickle
import os

drive.mount('/content/drive')

# Step 2: Load Data and Precomputed Models
X_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/X_train_clean.npy')
X_train_fgsm = np.load('/content/drive/My Drive/AI_Security_Project/X_train_fgsm.npy')
y_train_clean = np.load('/content/drive/My Drive/AI_Security_Project/y_train_clean.npy')
X_test = np.load('/content/drive/My Drive/AI_Security_Project/X_test.npy')
y_test = np.load('/content/drive/My Drive/AI_Security_Project/y_test.npy')
X_clean_hd = np.load('/content/drive/My Drive/AI_Security_Project/hai_clean_fgsm.npy')
X_fgsm_hd = np.load('/content/drive/My Drive/AI_Security_Project/hai_poisoned_fgsm.npy')

with open('/content/drive/My Drive/AI_Security_Project/qtp_fgsm.pkl', 'rb') as f:
    qtp = pickle.load(f)
with open('/content/drive/My Drive/AI_Security_Project/nsfe_fgsm.pkl', 'rb') as f:
    nsfe = pickle.load(f)
with open('/content/drive/My Drive/AI_Security_Project/are_fgsm.pkl', 'rb') as f:
    are_model = pickle.load(f)
imlc = tf.keras.models.load_model('/content/drive/My Drive/AI_Security_Project/imlc_fgsm.h5', custom_objects={'IMLC': IMLC}) if os.path.exists('/content/drive/My Drive/AI_Security_Project/imlc_fgsm.h5') else IMLC()

# Step 3: FGSM Beast Corrector with Incremental Learning
def fgsm_beast_corrector(X_poisoned, y_clean, X_test, y_test, incremental=True):
    print("Running FGSM Beast Corrector...")

    # QTP Purification
    X_poisoned_scaled = scaler.transform(X_poisoned)
    X_qtp_corrected = qtp(X_poisoned_scaled)
    X_qtp_corrected = scaler.inverse_transform(X_qtp_corrected)

    # HAI Isolation
    X_fgsm_hd_corrected = X_fgsm_hd * (np.linalg.norm(X_clean_hd, axis=1, keepdims=True) / np.linalg.norm(X_fgsm_hd, axis=1, keepdims=True))
    X_hai_corrected = np.dot(X_fgsm_hd_corrected, projector.components_.T)  # Inverse projection

    # NSFE Refinement
    X_nsfe_corrected = nsfe(X_poisoned_scaled)
    X_nsfe_corrected = scaler.inverse_transform(X_nsfe_corrected)

    # Combine with IMLC Weights
    scores = np.vstack([X_qtp_corrected, X_hai_corrected, X_nsfe_corrected]).T
    weights = imlc(scores)
    X_corrected = tf.reduce_sum(scores * weights, axis=1).numpy()

    # ARE Retraining
    are_model.fit(X_corrected, y_clean)
    y_pred = are_model.predict(X_test)
    accuracy = accuracy_score(y_test, y_pred)
    print(f"FGSM Corrected Accuracy: {accuracy*100:.2f}%")

    # Incremental Update
    if incremental:
        dataset = tf.data.Dataset.from_tensor_slices((X_poisoned_scaled, X_corrected)).batch(40000).prefetch(tf.data.AUTOTUNE)
        optimizer = tf.keras.optimizers.Adam(learning_rate=0.001)
        for epoch in range(3):
            total_loss = 0
            for batch_x, batch_y in dataset:
                with tf.GradientTape() as tape:
                    qtp_out = qtp(batch_x)
                    nsfe_out = nsfe(batch_x)
                    scores_batch = tf.stack([qtp_out, batch_x, nsfe_out], axis=1)  # HAI not re-trained, use original
                    weights_batch = imlc(scores_batch)
                    corrected_batch = tf.reduce_sum(scores_batch * weights_batch, axis=1)
                    loss = tf.reduce_mean(tf.square(corrected_batch - batch_y))
                grads = tape.gradient(loss, [qtp.trainable_variables, nsfe.trainable_variables, imlc.trainable_variables])
                optimizer.apply_gradients(zip(grads[0], qtp.trainable_variables))
                optimizer.apply_gradients(zip(grads[1], nsfe.trainable_variables))
                optimizer.apply_gradients(zip(grads[2], imlc.trainable_variables))
                total_loss += loss.numpy()
            print(f"Incremental Epoch {epoch+1}, Loss: {total_loss:.4f}")

    # Save Updated Models
    with open('/content/drive/My Drive/AI_Security_Project/qtp_fgsm.pkl', 'wb') as f:
        pickle.dump(qtp, f)
    with open('/content/drive/My Drive/AI_Security_Project/nsfe_fgsm.pkl', 'wb') as f:
        pickle.dump(nsfe, f)
    with open('/content/drive/My Drive/AI_Security_Project/are_fgsm.pkl', 'wb') as f:
        pickle.dump(are_model, f)
    imlc.save_weights('/content/drive/My Drive/AI_Security_Project/imlc_fgsm.h5')
    print("FGSM Beast Corrector models saved to Drive.")

    return X_corrected, are_model

# Step 4: Run Corrector
X_corrected_fgsm, are_model_fshm = fgsm_beast_corrector(X_train_fgsm, y_train_clean, X_test, y_test)

# Cleanup
del X_train_clean, X_train_fgsm, y_train_clean, X_test, y_test, X_clean_hd, X_fgsm_hd, qtp, nsfe, are_model, imlc, X_corrected_fgsm
tf.keras.backend.clear_session()
print("FGSM Beast Corrector completed, RAM cleared. Files safe in Google Drive.")